In [5]:
import numpy as np
import plotly.graph_objects as go
import plotly.express as px
import json
import os
import pandas as pd


folder = 'results1 copy/ocar_ETTh2_pl24_olfull_optadam_tb1_2025_08_12_02_53_2f3a'
feature = 1

mae_cumul = np.load(folder + '/mae.npy')
mse_cumul = np.load(folder + '/mse.npy')
metrics = np.load(folder + '/metrics.npy')
preds = np.load(folder + '/preds.npy')
trues = np.load(folder + '/trues.npy')
with open(folder + '/args.json') as f:
    args = json.load(f)

print('lr: ', args['online_lr'], 'regul ', args['OCAR_regul'], 'regul_last', args['OCAR_regul_last'])

print('MAE: ', metrics[0, 0], ' MSE: ', metrics[0, 1]) 


fig = go.Figure()
fig.add_trace(go.Scatter(x=np.arange(len(mae_cumul[0])), y=mae_cumul[0], mode='lines', name='MAE'))
fig.add_trace(go.Scatter(x=np.arange(len(mse_cumul[0])), y=mse_cumul[0], mode='lines', name='MSE'))
fig.show()

fig = go.Figure()
fig.add_trace(go.Scatter(x=np.arange(len(preds[0, :, feature])), y=preds[0, :, feature], mode='lines', name='Predictions'))
fig.add_trace(go.Scatter(x=np.arange(len(trues[0, :, feature])), y=trues[0, :, feature], mode='lines', name='True'))
fig.show()

max = 0
feat = 0
for i in range(preds.shape[2]):
    mse = np.mean((preds[0, :, i] - trues[0, :, i]) ** 2)
    if mse > max:
        max = mse
        feat = i
print('Max MSE: ', max, ' for feature ', feat)
fig = go.Figure()
fig.add_trace(go.Scatter(x=np.arange(len(preds[0, :, feat])), y=preds[0, :, feat], mode='lines', name='Predictions'))
fig.add_trace(go.Scatter(x=np.arange(len(trues[0, :, feat])), y=trues[0, :, feat], mode='lines', name='True'))
fig.show()

    

    






lr:  0.00829045918485869 regul  0.01225809021690695 regul_last 0.1
MAE:  0.4686342840945996  MSE:  2.064644323559432


Max MSE:  17.367144  for feature  166


In [1]:
import os
import json
import numpy as np
import pandas as pd
import datetime
# Base results directory
BASE_DIR = 'results1 copy'

# %% [markdown]
# ## 2. Collect all records

# %%
records = []

# iterate subdirectories
for root, dirs, files in os.walk(BASE_DIR):
    if 'args.json' in files and 'metrics.npy' in files:
        # 1. parse the folder basename
        folder = os.path.basename(root)
        parts = folder.split('_')
        # assume last 6 parts are [YYYY,MM,DD,HH,MM,<run_id>]
        date_str = '_'.join(parts[-6:-1])
        timestamp = datetime.datetime.strptime(date_str, '%Y_%m_%d_%H_%M')
        
        # 2. load args & metrics
        with open(os.path.join(root, 'args.json'), 'r') as f:
            args = json.load(f)
        mae, mse = np.load(os.path.join(root, 'metrics.npy'))[0,:2]
        
        # 3. build record, including the parsed timestamp
        rec = {
            'method':          args.get('method'),
            'data':            args.get('data'),
            'ng_only_last':    args.get('ng_only_last'),
            'deg_f':           args.get('deg_f'),
            'MAE':             mae,
            'MSE':             mse,
            'run_timestamp':   timestamp,              # new
            'run_date':        timestamp.date()        # if you only care about the date
        }
        records.append(rec)

# 4. DataFrame
df = pd.DataFrame.from_records(records)

# 5. Pivot including the date
table = df.pivot_table(
    index=['method', 'run_date', 'ng_only_last', 'deg_f'],
    columns='data',
    values=['MAE', 'MSE']
).sort_index()

display(table)


MAE                      \
data                                            ECL     ETTh1     ETTh2   
method     run_date   ng_only_last deg_f                                  
derpp      2025-07-01 False        5.0     1.268478  0.567357  0.538215   
er         2025-07-30 False        100.0   1.358159  0.563153  0.540723   
fsnet      2025-07-28 False        100.0   1.313252  0.392005  0.448966   
ocar       2025-07-04 False        100.0   0.636314  0.444600  0.465664   
                      True         100.0        NaN  0.464396  0.494709   
           2025-07-28 False        20.0    1.465915  0.351605  0.566802   
                                   100.0        NaN       NaN       NaN   
                      True         20.0         NaN  0.350305  0.511054   
                                   100.0        NaN       NaN       NaN   
           2025-08-12 False        20.0         NaN  0.435079  0.468425   
                      True         20.0         NaN  0.392172       NaN   
ocar_derpp 2025-07-04 False        100.0   1.353947  0.628395  0.569986   
           2025-07-25 True         100.0   1.271308  0.597299  0.530057   
ocar_fsnet 2025-07-04 False        100.0   1.099755  0.368288  0.457904   
           2025-07-24 False        100.0        NaN       NaN  0.474814   
                      True         100.0        NaN  0.365335  0.433125   
           2025-07-25 False        100.0   1.174515  0.373675       NaN   
                      True         100.0   1.204701       NaN       NaN   
ocar_temp  2025-08-14 False        20.0    1.387187  0.350435  0.428007   
           2025-08-15 False        1000.0  0.698099  0.356636       NaN   

                                                                         \
data                                          ETTm1       Toy      ToyG   
method     run_date   ng_only_last deg_f                                  
derpp      2025-07-01 False        5.0     0.317946  0.876833  0.862191   
er         2025-07-30 False        100.0   0.330650  0.879936  0.866041   
fsnet      2025-07-28 False        100.0   0.252608  0.756120  0.753504   
ocar       2025-07-04 False        100.0   0.300301  0.871941  0.860963   
                      True         100.0   0.312684  0.881197  0.869165   
           2025-07-28 False        20.0         NaN  0.795209  0.783357   
                                   100.0   0.213020       NaN       NaN   
                      True         20.0         NaN  0.791300  0.782519   
                                   100.0   0.242600       NaN       NaN   
           2025-08-12 False        20.0    0.221673  0.827934  0.815787   
                      True         20.0    0.274189  0.813192  0.803346   
ocar_derpp 2025-07-04 False        100.0   0.288888  0.841060  0.832748   
           2025-07-25 True         100.0   0.291651  0.842418  0.834019   
ocar_fsnet 2025-07-04 False        100.0   0.245419  0.732533  0.732770   
           2025-07-24 False        100.0        NaN       NaN       NaN   
                      True         100.0        NaN       NaN       NaN   
           2025-07-25 False        100.0   0.250062  0.732952  0.727754   
                      True         100.0   0.249630  0.739056  0.742519   
ocar_temp  2025-08-14 False        20.0    0.203049  0.805148  0.785147   
           2025-08-15 False        1000.0  0.207539  0.860240  0.845795   

                                                                      MSE  \
data                                        Traffic       WTH         ECL   
method     run_date   ng_only_last deg_f                                    
derpp      2025-07-01 False        5.0     0.371581  0.335206   10.628339   
er         2025-07-30 False        100.0   0.394982  0.351697   12.238909   
fsnet      2025-07-28 False        100.0   0.410208  0.278598    8.485181   
ocar       2025-07-04 False        100.0   0.415373  0.296644    6.203736   
                      True         100.0        NaN      

In [ ]:
import pandas as pd
import matplotlib.pyplot as plt

df_complete = pd.read_csv('grad_norm_history.csv')

for k in [0.001, 0.1, 1]:
    j = 1
    i = 5
    df = df_complete[(df_complete['deg_f'] == i) & (df_complete['scale'] == j ) & (df_complete['regul'] == k)]

    #Do the same plot with plotly
    import plotly.express as px
    import plotly.graph_objects as go
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=df['input_norm'], y=df['regularized_grad_norm'], mode='markers', name='Natural Gradient'))
    fig.add_trace(go.Scatter(x=df['input_norm'], y=df['original_grad_norm'], mode='markers', name='Original Gradient'))
    fig.update_xaxes(type="log")
    fig.update_yaxes(type="log")
    fig.update_layout(
                        xaxis_title='Input Norm',
                        yaxis_title='Gradient Norm',
                        title='Gradient Norms for ' + str(i))
    fig.show()

    fig = go.Figure()
    fig.add_trace(go.Scatter(x=df['target_norm'], y=df['regularized_grad_norm'], mode='markers', name='Natural Gradient'))
    fig.add_trace(go.Scatter(x=df['target_norm'], y=df['original_grad_norm'], mode='markers', name='Original Gradient'))
    fig.update_xaxes(type="log")
    fig.update_yaxes(type="log")
    fig.update_layout(
                        xaxis_title='Error Norm',
                        yaxis_title='Gradient Norm',
                        title='Gradient Norms for ' + str(i))
    fig.show()


fig = go.Figure()
for i in [5, 10, 20]:
    j = 1
    k = 0.001
    df = df_complete[(df_complete['deg_f'] == i) & (df_complete['scale'] == j ) & (df_complete['regul'] == k)]
    df2 = df.sort_values(by=['target_norm'])
    fig.add_trace(go.Scatter(x=df2['target_norm'], y=df2['regularized_grad_norm'].rolling(window=100).mean(), mode='lines', name='deg_f ' + str(i)))
    fig.update_xaxes(type="log")
fig.show()

fig = go.Figure()
for j in [0.1, 1, 10]:
    i = 5
    k = 0.001
    df = df_complete[(df_complete['deg_f'] == i) & (df_complete['scale'] == j ) & (df_complete['regul'] == k)]
    df2 = df.sort_values(by=['target_norm'])
    fig.add_trace(go.Scatter(x=df2['target_norm'], y=df2['regularized_grad_norm'].rolling(window=100).mean(), mode='lines', name='scale' + str(j)))
    fig.update_xaxes(type="log")
fig.show()

fig = go.Figure()
for k in [0.001, 0.1, 1]:
    j = 1
    i = 5
    df = df_complete[(df_complete['deg_f'] == i) & (df_complete['scale'] == j ) & (df_complete['regul'] == k)]
    df2 = df.sort_values(by=['target_norm'])
    fig.add_trace(go.Scatter(x=df2['target_norm'], y=df2['regularized_grad_norm'].rolling(window=100).mean(), mode='lines', name='regul ' + str(k)))
    fig.update_xaxes(type="log")
fig.show()

#########################
fig = go.Figure()
for i in [5, 10, 20]:
    j = 1
    k = 0.001
    df = df_complete[(df_complete['deg_f'] == i) & (df_complete['scale'] == j ) & (df_complete['regul'] == k)]
    df2 = df.sort_values(by=['input_norm'])
    fig.add_trace(go.Scatter(x=df2['input_norm'], y=df2['regularized_grad_norm'].rolling(window=100).mean(), mode='lines', name='deg_f ' + str(i)))
    fig.update_xaxes(type="log")
fig.show()

fig = go.Figure()
for j in [0.1, 1, 10]:
    i = 5
    k = 0.001
    df = df_complete[(df_complete['deg_f'] == i) & (df_complete['scale'] == j ) & (df_complete['regul'] == k)]
    df2 = df.sort_values(by=['input_norm'])
    fig.add_trace(go.Scatter(x=df2['input_norm'], y=df2['regularized_grad_norm'].rolling(window=100).mean(), mode='lines', name='scale' + str(j)))
    fig.update_xaxes(type="log")
fig.show()

fig = go.Figure()
for k in [0.001, 0.1, 1]:
    j = 1
    i = 5
    df = df_complete[(df_complete['deg_f'] == i) & (df_complete['scale'] == j ) & (df_complete['regul'] == k)]
    df2 = df.sort_values(by=['input_norm'])
    fig.add_trace(go.Scatter(x=df2['input_norm'], y=df2['regularized_grad_norm'].rolling(window=100).mean(), mode='lines', name='regul ' + str(k)))
    fig.update_xaxes(type="log")
fig.show()


